In [ ]:
pip install pycocotools

In [ ]:

from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
from pycocotools.coco import COCO
import requests
import os

# Specify the COCO dataset annotations and images URLs
annotations_url = "http://images.cocodataset.org/annotations/annotations_trainval2014.zip"
images_train_url = "http://images.cocodataset.org/zips/train2014.zip"

# Specify the local directory to download the data
data_dir = "./coco_data"

# Create the local directory if it doesn't exist
os.makedirs(data_dir, exist_ok=True)

# Download the annotations file
annotations_zip_path = os.path.join(data_dir, "annotations_trainval2014.zip")
annotations_file_path = os.path.join(data_dir, "annotations")
if not os.path.exists(annotations_file_path):
    print("Downloading COCO annotations...")
    with requests.get(annotations_url, stream=True) as response:
        with open(annotations_zip_path, "wb") as file:
            for chunk in response.iter_content(chunk_size=1024):
                if chunk:
                    file.write(chunk)

# Extract the annotations file
if not os.path.exists(annotations_file_path):
    import zipfile

    print("Extracting COCO annotations...")
    with zipfile.ZipFile(annotations_zip_path, "r") as zip_ref:
        zip_ref.extractall(data_dir)

# Download the training images file
images_train_zip_path = os.path.join(data_dir, "train2014.zip")
images_train_folder_path = os.path.join(data_dir, "train2014")
if not os.path.exists(images_train_folder_path):
    print("Downloading COCO training images...")
    with requests.get(images_train_url, stream=True) as response:
        with open(images_train_zip_path, "wb") as file:
            for chunk in response.iter_content(chunk_size=1024):
                if chunk:
                    file.write(chunk)

# Extract the training images file
if not os.path.exists(images_train_folder_path):
    print("Extracting COCO training images...")
    with zipfile.ZipFile(images_train_zip_path, "r") as zip_ref:
        zip_ref.extractall(data_dir)

# Initialize COCO with the downloaded annotations
coco = COCO(os.path.join(annotations_file_path, "instances_train2014.json"))

# Get the list of image IDs for the training set
image_ids = coco.getImgIds()

# Print the number of images in the training set
print("Number of training images:", len(image_ids))


Extracting COCO annotations...
Extracting COCO training images...
loading annotations into memory...
Done (t=17.72s)
creating index...
index created!
Number of training images: 82783


Import all the necessary packages

In [ ]:
# Install necessary packages in your Colab notebook
!pip install tensorflow
!pip install keras
!pip install nltk
!pip install numpy
!pip install matplotlib
!pip install Pillow
!pip install scikit-learn

Package installation and import statements


In [ ]:
# Import necessary packages
import numpy as np
import matplotlib.pyplot as plt
import nltk
from PIL import Image
from nltk.tokenize import word_tokenize
from nltk.translate.bleu_score import sentence_bleu
from sklearn.model_selection import train_test_split

import tensorflow as tf
from tensorflow.keras.preprocessing.image import load_img, img_to_array
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Dense, LSTM, Embedding, Dropout, add
from tensorflow.keras.applications.inception_v3 import InceptionV3, preprocess_input

Data cleaning and preprocessing.



In [ ]:
import os
import json

annotations_directory = "/content/drive/MyDrive/coco capstone project /annotations_trainval2014"

# List files in the directory
files_in_directory = os.listdir(annotations_directory)
print("Files in the directory:", files_in_directory)

# Assuming you choose a specific file, update the annotations_path
chosen_file = "your_chosen_annotations_file.json"
annotations_path = os.path.join(annotations_directory, chosen_file)

# Check if the file exists
if os.path.exists(annotations_path):
    with open(annotations_path, "r") as f:
        annotations = json.load(f)

    # Extract relevant information from annotations
    images_info = annotations['images']
    annotations_info = annotations['annotations']

    # Create a dictionary to map image IDs to their captions
    image_captions = {}
    for annotation in annotations_info:
        image_id = annotation['image_id']
        caption = annotation['caption']
        if image_id not in image_captions:
            image_captions[image_id] = []
        image_captions[image_id].append(caption)

    # Data cleaning and preprocessing
    # Perform any necessary steps based on your requirements

    # Confirm that images_info and image_captions are loaded correctly
    print(images_info[:5])  # Display the first 5 entries in images_info
    print(list(image_captions.keys())[:5])  # Display the image IDs of the first 5 entries in image_captions
else:
    print(f"Annotations file not found at {annotations_path}")


Files in the directory: ['captian_val2014.csv', 'instances_train014.csv', 'instances_val2014.csv', 'person_keypoints_train2014.csv', 'person_keypoints_val2014.csv', 'annotations']
Annotations file not found at /content/drive/MyDrive/coco capstone project /annotations_trainval2014/your_chosen_annotations_file.json


In [ ]:
from tensorflow.keras.preprocessing.image import load_img, img_to_array
from tensorflow.keras.applications.inception_v3 import preprocess_input
# Define image directory
image_dir = "/content/drive/MyDrive/coco capstone project /test2014"

# Load and preprocess images
def load_and_preprocess_images(image_dir, image_ids):
    images = {}
    for image_id in image_ids:
        # Construct the image path
        image_path = f"{image_dir}COCO_train2014_{str(image_id).zfill(12)}.jpg"
        print(f"Trying to load image: {image_path}")
        try:
            # Load and preprocess the image
            img = load_img(image_path, target_size=(299, 299))  # Adjust target_size as needed
            img_array = img_to_array(img)
            img_array = preprocess_input(img_array)
            images[image_id] = img_array
        except Exception as e:
            print(f"Error loading image: {image_path}")
            print(e)
    return images


# Example: Load and preprocess a subset of images
sample_image_ids = [72]  # Adjust the image ID as needed
sample_images = load_and_preprocess_images(image_dir, sample_image_ids)

Trying to load image: /content/drive/MyDrive/coco capstone project /test2014COCO_train2014_000000000072.jpg
Error loading image: /content/drive/MyDrive/coco capstone project /test2014COCO_train2014_000000000072.jpg
[Errno 2] No such file or directory: '/content/drive/MyDrive/coco capstone project /test2014COCO_train2014_000000000072.jpg'


Text Tokenization:

In [ ]:
# Assuming you have loaded COCO annotations and created image_captions as described in previous steps
image_captions = {
    1: ["A cat sitting on the sofa", "A cat looking at the camera"],
    2: ["A dog playing in the park", "A happy dog"],
    # Add more image IDs and captions as needed
}

# Tokenize captions
all_captions = [caption for captions_list in image_captions.values() for caption in captions_list]
tokenizer = Tokenizer()
tokenizer.fit_on_texts(all_captions)

# Vocabulary size
vocab_size = len(tokenizer.word_index) + 1

print("Vocabulary size:", vocab_size)

Vocabulary size: 15


Padding and Sequencing Captions:

In [ ]:
max_length = 100  # Set an appropriate value for max_length

# Generate input sequences and target sequences for LSTM
input_sequences = []
target_sequences = []

for image_id, captions_list in image_captions.items():
    for caption in captions_list:
        # Convert caption text to sequence of integers
        caption_sequence = tokenizer.texts_to_sequences([caption])[0]

        # Generate input and target sequences
        for i in range(1, len(caption_sequence)):
            input_seq = caption_sequence[:i]
            target_seq = caption_sequence[i]

            # Pad sequences to a fixed length
            input_seq = pad_sequences([input_seq], maxlen=max_length, padding='post')[0]

            # Store input and target sequences
            input_sequences.append(input_seq)
            target_sequences.append(target_seq)

# Convert sequences to numpy arrays
X = np.array(input_sequences)
y = np.array(target_sequences)

Extracting the feature vector from all images

In [ ]:
import os
import numpy as np
import tensorflow as tf
from tensorflow.keras.applications.inception_v3 import InceptionV3, preprocess_input
from tensorflow.keras.models import Model
from tensorflow.keras.preprocessing.image import load_img, img_to_array

# Function to extract features from an image
def extract_features(image_path, model):
    try:
        img = load_img(image_path, target_size=(299, 299))
        img_array = img_to_array(img)
        img_array = np.expand_dims(img_array, axis=0)
        img_array = preprocess_input(img_array)
        features = model.predict(img_array)
        return features.flatten()
    except Exception as e:
        print(f"Error processing image {image_path}: {e}")
        return np.zeros((desired_shape,))  # Replace 'desired_shape' with the expected shape

# Load InceptionV3 model pre-trained on ImageNet
base_model = InceptionV3(weights='imagenet')
model = Model(inputs=base_model.input, outputs=base_model.layers[-2].output)

# Path to the COCO 2014 dataset images
dataset_path = "/content/drive/MyDrive/coco capstone project /test2014"  # Update this path

# List all image files in the dataset path
image_files = [f for f in os.listdir(dataset_path) if f.endswith('.jpg')]

# Create a list to store image paths and feature vectors
data = {'image_path': [], 'image_features': []}

# Extract features for each image and store in the list
for image_file in image_files:
    image_path = os.path.join(dataset_path, image_file)
    features = extract_features(image_path, model)
    data['image_path'].append(image_path)
    data['image_features'].append(features)
    print(f"Processed {image_file}, Feature Shape: {features.shape}")

# Filter out entries with empty feature vectors
non_empty_entries = [i for i, features in enumerate(data['image_features']) if np.any(features)]
data['image_path'] = [data['image_path'][i] for i in non_empty_entries]
data['image_features'] = [data['image_features'][i] for i in non_empty_entries]

# Convert the 'image_features' column to a NumPy array
if data['image_features']:
    feature_vectors = np.vstack(data['image_features'])
    # Save the feature vectors to a file if needed
    np.save("image_features.npy", feature_vectors)
else:
    print("No valid feature vectors to concatenate.")


96112376/96112376 [==============================] - 0s 0us/step
No valid feature vectors to concatenate.


In [ ]:
import os
import numpy as np
from tqdm import tqdm
from tensorflow.keras.applications.inception_v3 import InceptionV3, preprocess_input
from tensorflow.keras.models import Model
from tensorflow.keras.preprocessing.image import load_img, img_to_array

# Load InceptionV3 model pre-trained on ImageNet
base_model = InceptionV3(weights='imagenet')
model = Model(inputs=base_model.input, outputs=base_model.layers[-2].output)

# Function to extract features from an image
def extract_features(image_path):
    try:
        img = load_img(image_path, target_size=(299, 299))
        img_array = img_to_array(img)
        img_array = np.expand_dims(img_array, axis=0)
        img_array = preprocess_input(img_array)
        features = model.predict(img_array)
        return features.flatten()
    except Exception as e:
        print(f"Error processing image {image_path}: {e}")
        return np.zeros((desired_shape,))  # Replace 'desired_shape' with the expected shape

# Define the directory containing the images
image_dir = "/content/drive/MyDrive/coco capstone project /test2014/test2014"  # Replace with the path to your dataset

# Get a list of all image files in the directory
image_files = [f for f in os.listdir(image_dir) if f.endswith(".jpg")]

# Initialize an empty dictionary to store image features
image_features_dict = {}

# Iterate over each image file
for image_file in tqdm(image_files, desc="Extracting Features", unit="image"):
    # Construct the full path to the image file
    image_path = os.path.join(image_dir, image_file)

    # Extract features for the current image
    image_features = extract_features(image_path)

    # Store the features in the dictionary using the image file name as the key
    image_features_dict[image_file] = image_features

# Convert the dictionary to a NumPy array
image_features_array = np.array(list(image_features_dict.values()))

# Specify the directory where you want to save the file
save_dir = "/content/drive/MyDrive/coco capstone project"  # Replace with your desired directory

# Create the directory if it does not exist
os.makedirs(save_dir, exist_ok=True)

# Save the extracted features to a file in the specified directory
np.save(os.path.join(save_dir, "image_features.npy"), image_features_array)


Extracting Features:   0%|          | 0/10560 [00:00<?, ?image/s]

1/1 [==============================] - 4s 4s/step


Extracting Features:   0%|          | 1/10560 [00:04<13:39:08,  4.65s/image]

1/1 [==============================] - 0s 418ms/step


Extracting Features:   0%|          | 2/10560 [00:06<8:20:11,  2.84s/image] 

...

Extracting Features: 100%|█████████▉| 10558/10560 [1:40:53<00:01,  1.49image/s]

1/1 [==============================] - 0s 272ms/step


Extracting Features: 100%|█████████▉| 10559/10560 [1:40:53<00:00,  1.68image/s]

1/1 [==============================] - 0s 409ms/step


Extracting Features: 100%|██████████| 10560/10560 [1:40:54<00:00,  1.74image/s]


Loading dataset for Training the model


In [ ]:
from pycocotools.coco import COCO
import numpy as np
import random

# Specify the paths to the COCO dataset annotations and images
annotations_path = '/content/drive/MyDrive/coco capstone project /annotations_trainval2014.zip'
images_folder_path = '/content/drive/MyDrive/coco capstone project /test2014/test2014'

# Initialize the COCO API for annotations
coco = COCO(annotations_path)

# Get all image ids
all_image_ids = list(coco.imgs.keys())

# Shuffle the image ids to create a random split
random.seed(42)
random.shuffle(all_image_ids)

# Define the split ratio for training and validation
split_ratio = 0.8
split_index = int(len(all_image_ids) * split_ratio)

# Split the image ids into training and validation sets
train_image_ids = all_image_ids[:split_index]
val_image_ids = all_image_ids[split_index:]

# Load annotations for training and validation sets
train_annotations = coco.loadAnns(coco.getAnnIds(imgIds=train_image_ids))
val_annotations = coco.loadAnns(coco.getAnnIds(imgIds=val_image_ids))

# Create lists of image paths and corresponding captions for training and validation
train_image_paths = [os.path.join(images_folder_path, coco.imgs[image_id]['file_name']) for image_id in train_image_ids]
train_captions = [annotation['caption'] for annotation in train_annotations]

val_image_paths = [os.path.join(images_folder_path, coco.imgs[image_id]['file_name']) for image_id in val_image_ids]
val_captions = [annotation['caption'] for annotation in val_annotations]

# Print the number of samples in each set
print(f"Number of training samples: {len(train_image_paths)}")
print(f"Number of validation samples: {len(val_image_paths)}")

loading annotations into memory...


UnicodeDecodeError: ignored

Tokenizing the vocabulary

In [ ]:
from pycocotools.coco import COCO
from nltk.tokenize import word_tokenize
from collections import Counter

# Load COCO annotations
annotations_path = '/content/coco_data/annotations'
coco = COCO(annotations_path)

# Get all captions from the training set
train_image_ids = coco.getImgIds()
train_captions = [annotation['caption'] for image_id in train_image_ids for annotation in coco.imgToAnns[image_id]]

# Tokenize captions
tokenized_captions = [word_tokenize(caption.lower()) for caption in train_captions]

# Flatten the list of tokenized captions
all_tokens = [token for tokens in tokenized_captions for token in tokens]

# Count token occurrences
token_counter = Counter(all_tokens)

# Create a vocabulary based on the most common tokens
vocab_size = 5000  # Set the desired vocabulary size
vocab = [token for token, _ in token_counter.most_common(vocab_size)]

# Create a dictionary to map tokens to integer indices
word_to_index = {word: index + 1 for index, word in enumerate(vocab)}
index_to_word = {index + 1: word for index, word in enumerate(vocab)}

# Print the size of the vocabulary
print(f"Vocabulary size: {len(vocab)}")

# Save the vocabulary and mappings to files if needed
with open('vocab.txt', 'w') as f:
    f.write('\n'.join(vocab))

with open('word_to_index.json', 'w') as f:
    json.dump(word_to_index, f)

with open('index_to_word.json', 'w') as f:
    json.dump(index_to_word, f)


Create Data Generator

In [ ]:
import os
import numpy as np
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.preprocessing.image import load_img, img_to_array
from pycocotools.coco import COCO
from nltk.tokenize import word_tokenize

class DataGenerator(tf.keras.utils.Sequence):
    def __init__(self, coco, image_dir, captions, word_to_index, batch_size, max_length):
        self.coco = coco
        self.image_dir = image_dir
        self.captions = captions
        self.word_to_index = word_to_index
        self.batch_size = batch_size
        self.max_length = max_length
        self.index_to_word = {index: word for word, index in word_to_index.items()}
        self.on_epoch_end()

    def __len__(self):
        return int(np.ceil(len(self.captions) / self.batch_size))

    def __getitem__(self, index):
        # Get the current batch indices
        batch_indices = self.indices[index * self.batch_size:(index + 1) * self.batch_size]

        # Initialize arrays for image features and captions
        X_images = np.zeros((len(batch_indices), 299, 299, 3))
        X_captions = np.zeros((len(batch_indices), self.max_length))
        y = np.zeros((len(batch_indices), len(self.word_to_index) + 1))

        for i, idx in enumerate(batch_indices):
            # Load and preprocess image
            image_id = self.captions[idx]['image_id']
            image_path = os.path.join(self.image_dir, self.coco.loadImgs(image_id)[0]['file_name'])
            img = load_img(image_path, target_size=(299, 299))
            img_array = img_to_array(img)
            img_array = img_array.reshape((1,) + img_array.shape)
            X_images[i] = img_array

            # Tokenize and pad caption sequence
            caption_tokens = word_tokenize(self.captions[idx]['caption'].lower())
            caption_sequence = [self.word_to_index.get(token, 0) for token in caption_tokens]
            X_captions[i, :len(caption_sequence)] = caption_sequence
            y[i] = to_categorical(caption_sequence + [0] * (self.max_length - len(caption_sequence)), len(self.word_to_index) + 1)

        return {'image_input': X_images, 'caption_input': X_captions}, {'output': y}

    def on_epoch_end(self):
        self.indices = np.arange(len(self.captions))
        np.random.shuffle(self.indices)

# Example usage
annotations_path = '/path/to/annotations_trainval2014.json'
image_dir = '/path/to/train2014/'
batch_size = 32
max_length = 20  # Set the maximum length of captions
coco = COCO(annotations_path)

# Assuming you have a list of captions
captions = coco.loadAnns(coco.getAnnIds())

# Create word_to_index mapping (you should have this from the tokenization step)
word_to_index = {...}

# Create data generator
data_generator = DataGenerator(coco, image_dir, captions, word_to_index, batch_size, max_length)

# You can now use this data generator to train your model with the fit method
# model.fit(data_generator, epochs=50, ...)


Defining the CNN-RNN model

In [ ]:
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Dense, LSTM, Embedding, Dropout
from tensorflow.keras.applications.inception_v3 import InceptionV3
from tensorflow.keras import layers

# Set the maximum length of captions
max_length = 20  # Adjust based on your dataset

# CNN (InceptionV3) for image feature extraction
image_input = Input(shape=(299, 299, 3), name='image_input')
base_model = InceptionV3(weights='imagenet', include_top=False)
image_features = base_model(image_input)
image_features = layers.GlobalAveragePooling2D()(image_features)

# RNN (LSTM) for sequence generation
caption_input = Input(shape=(max_length,), name='caption_input')
embedding_layer = Embedding(input_dim=vocab_size + 1, output_dim=300, input_length=max_length, mask_zero=True)(caption_input)
lstm_layer = LSTM(256)(embedding_layer)

# Combine image and caption features
merged = layers.concatenate([image_features, lstm_layer])
merged = Dropout(0.5)(merged)
output_layer = Dense(vocab_size + 1, activation='softmax', name='output')(merged)

# Create the final model
model = Model(inputs=[image_input, caption_input], outputs=output_layer)

# Compile the model
model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

# Display the model summary
model.summary()


TRAINING SECTION:
*Train the dataset images and Test with a minimum of 50 epochs

In [ ]:
# Set the number of training epochs
epochs = 50

# Train the model
model.fit(data_generator, epochs=epochs, verbose=1)

# Save the trained model
model.save('image_caption_model.h5')

In [ ]:
# Assuming you have split your data into training and validation sets
train_data_generator = DataGenerator(train_coco, image_dir, train_captions, word_to_index, batch_size, max_length)
valid_data_generator = DataGenerator(valid_coco, image_dir, valid_captions, word_to_index, batch_size, max_length)

# Train the model with validation data
model.fit(train_data_generator, epochs=epochs, validation_data=valid_data_generator, verbose=1)

 Test the model using different images to showcase captions correctly

In [ ]:
# Assuming you have a trained model (loaded_model) and a test data generator (test_data_generator)

# Load the trained model
loaded_model = tf.keras.models.load_model('image_caption_model.h5')

# Evaluate the model on the test data generator
evaluation_results = loaded_model.evaluate(test_data_generator)

# Display evaluation results
print("Test Loss:", evaluation_results[0])
print("Test Accuracy:", evaluation_results[1])

# Generate captions for sample images
num_samples = 5  # Number of images to showcase
for i in range(num_samples):
    # Assuming you have a function to load and preprocess a single image for testing
    test_image = load_and_preprocess_test_image()  # Implement this function based on your requirements
    test_image = np.expand_dims(test_image, axis=0)  # Add batch dimension

    # Use the model to predict captions
    predictions = loaded_model.predict([test_image, np.zeros((1, max_length))])

    # Convert predictions to text captions
    predicted_caption = decode_caption(predictions, index_to_word)  # Implement this function based on your setup

    # Display the predicted caption
    print(f"Image {i + 1}: {predicted_caption}")


*Executed code with image output to be submitted as a result.

In [ ]:
import matplotlib.pyplot as plt
from PIL import Image

# Assuming you have a trained model (loaded_model) and a function to preprocess test images (preprocess_test_image)
loaded_model = tf.keras.models.load_model('image_caption_model.h5')

# Function to preprocess a test image
def preprocess_test_image(image_path):
    img = tf.keras.preprocessing.image.load_img(image_path, target_size=(299, 299))
    img_array = tf.keras.preprocessing.image.img_to_array(img)
    img_array = np.expand_dims(img_array, axis=0)
    img_array = preprocess_input(img_array)
    return img_array

# Function to decode model predictions to text captions
def decode_caption(predictions, index_to_word):
    # Implement this function based on your specific setup
    # Convert the model predictions to a text caption
    return caption

# Sample image paths for testing
sample_image_paths = [
    '/path/to/test/image1.jpg',
    '/path/to/test/image2.jpg',
    '/path/to/test/image3.jpg',
    # Add more sample image paths as needed
]

# Display images with predicted captions
for image_path in sample_image_paths:
    # Preprocess the test image
    test_image = preprocess_test_image(image_path)

    # Use the model to predict captions
    predictions = loaded_model.predict([test_image, np.zeros((1, max_length))])

    # Decode the predicted captions
    predicted_caption = decode_caption(predictions, index_to_word)

    # Display the image with the predicted caption
    img = Image.open(image_path)
    plt.imshow(img)
    plt.title(f'Predicted Caption: {predicted_caption}')
    plt.axis('off')
    plt.show()
